In [1]:
import itertools
import matplotlib.pyplot as plt
import pandas as pd

%matplotlib inline

## Context

This notebook aims to show in which cases sklearn `auto` heuristic isn't optimal. A good default value should work well in most (if not all) regular cases. Experiments previously run explore the following settings:
- 5 datasets accounting for different data structures
- `n_samples` in `{10,000; 50,000; 100,000}`
- `n_features` in `[5; 10]` $\cup$ `{15, 20, 25, 30}`
- `algorithm` in `{'brute', 'kd_tree', 'ball_tree'}`
- `n_neighbors` in `{10, 100}`

With `n_jobs` and `n_threads` fixed to 1 and 8, respectively. To study the impact of using 8 threads in OpenMP/BLAS thread pools we also run the same experiments with the following changes:
- `n_features` in `{5, 10, 15, 20, 25, 30}`
- `algorithm` = `'brute'`
- `n_threads` in `{1, 8}`

Time reported are expressed in seconds.

## I - Preprocessing

Load experiments results.

In [2]:
results = pd.read_csv('results.csv')
results.head()

algorithm    dataset  n_features  n_jobs  n_neighbors  n_samples  n_threads  \
0     brute  covertype           5       1           10      10000          8   
1     brute  covertype           5       1           10      50000          8   
2     brute  covertype           5       1           10     100000          8   
3     brute  covertype           5       1          100      10000          8   
4     brute  covertype           5       1          100      50000          8   

   time_construction_mean  time_construction_std  time_querying_mean  \
0                0.000191               0.000092            1.380593   
1                0.000251               0.000009            6.355835   
2                0.000360               0.000007           10.067984   
3                0.000137               0.000004            1.072156   
4                0.000257               0.000006            6.000334   

   time_querying_std  
0           0.014017  
1           1.572117  
2           1.784639  
3           0.299842  
4           1.286787

Transform results dataframe in order to get, for a given experiment, each algorithm querying times on the same row.

In [3]:
to_drop = ['time_construction_mean', 'time_construction_std']
temp = results.drop(columns=to_drop).copy()

experiment_params = ['dataset', 'n_samples', 'n_features', 'n_neighbors']
parallel_params = ['n_jobs', 'n_threads']
params = experiment_params + parallel_params

algorithms = temp.algorithm.unique()

for i, algo in enumerate(algorithms):
    new_columns = {'time_querying_mean': f'{algo}_mean', 'time_querying_std': f'{algo}_std'}
    
    temp_ = temp.query('algorithm == @algo').copy()
    temp_.rename(columns=new_columns, inplace=True)
    temp_.drop(columns='algorithm', inplace=True)

    df = df.merge(temp_, how='outer') if i else temp_

df.head()

dataset  n_features  n_jobs  n_neighbors  n_samples  n_threads  \
0  covertype           5       1           10      10000          8   
1  covertype           5       1           10      50000          8   
2  covertype           5       1           10     100000          8   
3  covertype           5       1          100      10000          8   
4  covertype           5       1          100      50000          8   

   brute_mean  brute_std  kd_tree_mean  kd_tree_std  ball_tree_mean  \
0    1.380593   0.014017      0.339064     0.094828        0.400355   
1    6.355835   1.572117      2.813658     0.785814        1.316014   
2   10.067984   1.784639      5.414496     2.152798        2.449653   
3    1.072156   0.299842      0.549013     0.100955        0.687518   
4    6.000334   1.286787      2.013975     1.383395        1.517414   

   ball_tree_std  
0       0.052588  
1       0.088847  
2       0.708142  
3       0.132180  
4       0.035970

## II - `n_threads` effect on brute force

`'brute'` is using OpenMP/BLAS thread pools under the hoods, let's compare the use of `1` vs `8` threads by calculating their ratio.

In [4]:
n_features = list(range(5, 31, 5))
n_threads_unique = df.n_threads.unique()

for i, n_threads in enumerate(n_threads_unique):
    temp = results.drop(columns=to_drop).query(
        'algorithm == "brute" and '
        'n_features.isin(@n_features) and '
        'n_threads == @n_threads'
    ).copy()
    
    temp.rename(columns={'time_querying_mean': f'{n_threads}_threads_mean'}, inplace=True)
    temp.drop(columns=['n_threads', 'time_querying_std'], inplace=True)

    df_brute = df_brute.merge(temp, how='outer') if i else temp

n_threads_ratio = df_brute['8_threads_mean'] / df_brute['1_threads_mean']
n_threads_ratio.describe()

count    162.000000
mean       1.044964
std        0.053028
min        0.911334
25%        1.013390
50%        1.044797
75%        1.073403
max        1.218645
dtype: float64

Results can be surprising here in the sense that limiting ourself to 1 thread instead of 8 is actually slightly faster in more than 75% of our 162 experiments. More precisely, it's faster by an average factor of 1.04 ± 0.05

## III - Current sklearn heuristic

Quoting [sklearn meighbors documentation](https://scikit-learn.org/dev/modules/neighbors.html#choice-of-nearest-neighbors-algorithm):

> Currently, `algorithm = 'auto'` selects `'brute'` if , the input data is sparse, or `effective_metric_` isn’t in the `VALID_METRICS` list for either `'kd_tree'` or `'ball_tree'`. Otherwise, it selects the first out of `'kd_tree'` and `'ball_tree'` that has `effective_metric_` in its `VALID_METRICS` list. This choice is based on the assumption that the number of query points is at least the same order as the number of training points, and that `leaf_size` is close to its default value of `30`.

Which is translated in [sklearn source code](https://github.com/scikit-learn/scikit-learn/blob/95d4f0841/sklearn/neighbors/_base.py#L434) to:

```python
if self._fit_method == 'auto':
    # A tree approach is better for small number of neighbors,
    # and KDTree is generally faster when available
    if ((self.n_neighbors is None or
         self.n_neighbors < self._fit_X.shape[0] // 2) and
            self.metric != 'precomputed'):
        if self.effective_metric_ in VALID_METRICS['kd_tree']:
            self._fit_method = 'kd_tree'
        elif (callable(self.effective_metric_) or
                self.effective_metric_ in VALID_METRICS['ball_tree']):
            self._fit_method = 'ball_tree'
        else:
            self._fit_method = 'brute'
    else:
        self._fit_method = 'brute'
```

In the general case `n_neighbors` is smaller than `n_samples // 2` and `'kd_tree'` is choosen. We know that tree based methods suffer from high dimensionality datasets, especially when the intrinsic dimensionality is high. By not accounting for the data dimensionality, the heuristic often fail by a large margin when the data dimensionality is high. Estimating the intrinsic dimensionality is hard and costly, but `n_features` may bring information that could benefit the heuristic.

## IV - Ball tree

Let's calculate statistics about how often each method is the optimal choice as by how much.

In [5]:
n_features = list(range(5, 31, 5))
algorithms = results.algorithm.unique()
time_cols = [f'{algo}_mean' for algo in algorithms]

def speedup(row):
    speedup = row.median() / row.min()
    
    min_col = row.index[row == row.min()][0]
    min_algo = min_col[:min_col.rfind('_')]
    
    return speedup, min_algo

temp = df.dropna().query('n_features.isin(@n_features)')[time_cols].apply(speedup, axis=1)
temp = pd.DataFrame(temp.tolist(), columns=['speedup', 'min_algo'])

for algo in algorithms:
    temp_ = temp.query('min_algo == @algo')
    print(
        f'{algo} is the fastest querying method {len(temp_) / len(temp) * 100:.1f}% of the time '
        f'by an average factor of {temp_.speedup.mean():.1f} '
        f'±{temp_.speedup.std():.1f} on the second fastest'
    )

brute is the fastest querying method 50.0% of the time by an average factor of 2.8 ±2.2 on the second fastest
kd_tree is the fastest querying method 44.4% of the time by an average factor of 5.3 ±4.5 on the second fastest
ball_tree is the fastest querying method 5.6% of the time by an average factor of 1.3 ±0.5 on the second fastest


We observe that `'ball_tree'` is rarely the fastest method, and when it is, it's only by a small factor compared to other methods. Therefore, we are going to simplify the heuristic problem to a choice between `'brute'` and `'kd_tree'`, easing further analyses.

## V - K-d tree vs Brute force

Define plot utilities.

In [6]:
n_features = list(range(5, 31, 5))
temp = df.query('n_features.isin(@n_features) and n_threads == 8').copy()

params_gen = list(itertools.product(
    df.n_samples.unique(),
    df.n_neighbors.unique(),
))

Let's compare `'kd_tree'` and `'brute'` querying times.

In [7]:
algorithms = ['brute', 'kd_tree']

std_colors = plt.rcParams['axes.prop_cycle'].by_key()['color']

fig, axes = plt.subplots(3, 2, figsize=(23, 20), dpi=400)
axes = axes.ravel()

xmin = temp['n_features'].min()
xmax = temp['n_features'].max()
ymin = temp[[f'{algo}_mean' for algo in algorithms]].values.min()
ymax = temp[[f'{algo}_mean' for algo in algorithms]].values.max()

for ix, (n_samples, n_neighbors) in enumerate(params_gen):
    
    for ix_color, dataset in enumerate(temp.dataset.unique()):
        temp_ = temp.query(
            'dataset == @dataset and '
            'n_samples == @n_samples and '
            'n_neighbors == @n_neighbors'
        ).copy()

        for algo, linestyle in zip(algorithms, ['solid', 'dashed']):
            axes[ix].errorbar(
                temp_['n_features'],
                temp_[f'{algo}_mean'],
                yerr=temp_[f'{algo}_std'],
                color=std_colors[ix_color],
                linestyle=linestyle,
                label=f'{dataset} ({algo})'
            )
    
    axes[ix].grid(which='both', linestyle=':')
    axes[ix].legend(ncol=2, framealpha=1)
    axes[ix].set_title(f'n_samples = {n_samples:,}; n_neighbors = {n_neighbors}')
    axes[ix].set_xlabel('n_features')
    axes[ix].set_yscale('log')
    axes[ix].set_xlim(xmin, xmax)
    axes[ix].set_ylim(ymin, ymax)

fig.suptitle('K-d tree vs Brute force', fontsize=18)
plt.subplots_adjust(top=.94)

plt.savefig('img/kd_tree_vs_brute.png')

Observations:
- `'brute'` is mainly impacted by `n_samples`, data structure has little effects on it
- `'kd_tree'` is much faster with lower dataset intrinsic dimensionality or higher dataset sparsity
- `'kd_tree'` is slower when `n_neighbors` is high, in proportion to `n_samples` and `n_features`
- `'brute'` is more efficient than `'kd_tree'` when `n_features` is too high. The treshold mostly depends of the data structure and with a smaller impact from `n_samples` and `n_neighbors`

## VII - K-d tree vs Brute force — speedup ratio

In [8]:
temp['speedup'] = temp['kd_tree_mean'] / temp['brute_mean']

fig, axes = plt.subplots(3, 2, figsize=(23, 20), dpi=400)
axes = axes.ravel()

xmin, xmax = temp['n_features'].min(), temp['n_features'].max()
ymin, ymax = temp['speedup'].min(), temp['speedup'].max()

for ix, (n_samples, n_neighbors) in enumerate(params_gen):
    
    for dataset in temp.dataset.unique():
        temp_ = temp.query(
            'dataset == @dataset and '
            'n_samples == @n_samples and '
            'n_neighbors == @n_neighbors'
        ).copy()

        axes[ix].plot(temp_['n_features'], temp_['speedup'], label=dataset)
    
    axes[ix].fill([xmin, xmin, xmax, xmax], [1, ymax, ymax, 1], 'mistyrose')
    axes[ix].fill([xmin, xmin, xmax, xmax], [ymin, 1, 1, ymin], 'honeydew')
    axes[ix].grid(which='both', linestyle=':')
    axes[ix].legend(loc='upper left', framealpha=1)
    axes[ix].plot([xmin, xmax], [1, 1], color='black')
    axes[ix].set_title(f'n_samples = {n_samples:,}; n_neighbors = {n_neighbors}')
    axes[ix].set_xlabel('n_features')
    axes[ix].set_yscale('log')
    axes[ix].set_xlim(xmin, xmax)
    axes[ix].set_ylim(ymin, ymax)
    axes[ix].text(xmin, 1.1, 'brute is optimal', size=10)
    axes[ix].text(xmin, .8, 'kd_tree is optimal', size=10)

fig.suptitle('K-d tree vs Brute force — speedup ratio', fontsize=18)
plt.subplots_adjust(top=.94)

plt.savefig('img/kd_tree_vs_brute_speedup_ratio.png')